In [ ]:
!pip install opencv-python

In [1]:
!pip install opencv-python

   ---------------------------------------- 0.0/39.5 MB ? eta -:--:--
   ---------------------------------------- 0.0/39.5 MB ? eta -:--:--
    --------------------------------------- 0.8/39.5 MB 3.7 MB/s eta 0:00:11
   - -------------------------------------- 1.8/39.5 MB 5.9 MB/s eta 0:00:07
   --- ------------------------------------ 3.4/39.5 MB 5.3 MB/s eta 0:00:07
   ------- -------------------------------- 7.6/39.5 MB 9.2 MB/s eta 0:00:04
   --------- ------------------------------ 9.7/39.5 MB 9.4 MB/s eta 0:00:04
   ------------ --------------------------- 12.1/39.5 MB 9.7 MB/s eta 0:00:03
   -------------- ------------------------- 14.4/39.5 MB 10.0 MB/s eta 0:00:03
   ---------------- ----------------------- 16.3/39.5 MB 10.0 MB/s eta 0:00:03
   ------------------ --------------------- 18.6/39.5 MB 10.0 MB/s eta 0:00:03
   -------------------- ------------------- 20.4/39.5 MB 9.8 MB/s eta 0:00:02
   ---------------------- ----------------- 22.3/39.5 MB 9.7 MB/s eta 0:00:02
   -

Расширяем датасет + 5 аугментаций (размытие, яркость и контраст, сдвиг и поворот) + описания.
на входе исходная папка data c картинками и файл description2.csv. На выходе увеличенное количество картинок в папке data и дополненный csv - augmented_description2.csv

In [11]:
import pandas as pd
import os
import numpy as np
import cv2
from tensorflow.keras.preprocessing.image import load_img, img_to_array
import uuid
import random

def calculate_cosine_angles(image):
    gray = cv2.cvtColor(image, cv2.COLOR_RGB2GRAY)
    edges = cv2.Canny(gray, 50, 150, apertureSize=3)
    lines = cv2.HoughLines(edges, 1, np.pi / 180, 200)

    if lines is None:
        return np.array([])

    angles = []
    for line in lines:
        rho, theta = line[0]
        angles.append(theta)
    if len(angles) < 2:
        return np.array([])
    cosine_angles = []
    for i in range(len(angles)):
        for j in range(i + 1, len(angles)):
            cosine = np.cos(angles[i] - angles[j])
            cosine_angles.append(cosine)
    return np.array(cosine_angles)


def augment_image(img):
    """
    Применяет реалистичную аугментацию к изображению.

    Args:
        img (numpy.ndarray): Изображение в виде массива NumPy.

    Returns:
        numpy.ndarray: Аугментированное изображение.
    """
    img = np.array(img, dtype=np.float32)
    rows, cols, ch = img.shape

    # Размытие
    if random.random() < 0.5:  # 50% вероятность
        blur_size = random.randint(1, 3) * 2 + 1  # Нечетный размер ядра
        img = cv2.GaussianBlur(img, (blur_size, blur_size), 0)

    # Яркость и контраст
    if random.random() < 0.5:
        brightness = random.uniform(0.8, 1.2)
        contrast = random.uniform(0.8, 1.2)
        img = cv2.convertScaleAbs(img, alpha=contrast, beta=0)
        img = cv2.add(img, np.array([brightness * 255 - 255 if brightness > 1 else 0], dtype=np.float32))

    # Сдвиг и поворот (малые углы)
    if random.random() < 0.5:
        shift_x = random.randint(-10, 10)
        shift_y = random.randint(-10, 10)
        rotation = random.uniform(-5, 5)

        M = cv2.getRotationMatrix2D((cols / 2, rows / 2), rotation, 1)
        M[0, 2] += shift_x
        M[1, 2] += shift_y
        img = cv2.warpAffine(img, M, (cols, rows))

    return np.uint8(img)


def augment_and_extend_csv(input_csv, output_csv, output_dir, num_augmentations=5):
    """
    Расширяет CSV-файл, добавляя указанное количество аугментированных изображений для каждой строки.

    Args:
        input_csv (str): Путь к входному CSV-файлу.
        output_csv (str): Путь к выходному CSV-файлу.
        output_dir (str): Путь к директории для сохранения аугментированных изображений.
        num_augmentations (int): Количество аугментированных изображений для создания на каждое исходное.
    """

    df = pd.read_csv(input_csv)
    augmented_rows = []
    os.makedirs(output_dir, exist_ok=True)  # Создаем директорию, если ее нет

    for index, row in df.iterrows():
        img_path = row["filename"]
        if not os.path.exists(img_path):
            print(f"Файл не найден: {img_path}")
            continue

        img = load_img(img_path, target_size=(224, 224))  # Загружаем изображение
        img = img_to_array(img)  # Преобразуем в numpy массив

        for i in range(num_augmentations):
            aug_img = augment_image(img)  # Аугментируем изображение
            new_filename = f"{uuid.uuid4().hex}.jpg"  # Генерируем новое имя файла
            new_img_path = os.path.join(output_dir, new_filename)  # Формируем путь к новому файлу
            cv2.imwrite(new_img_path, aug_img)  # Сохраняем аугментированное изображение

            # Создаем новую строку в DataFrame, копируя данные из исходной
            new_row = row.copy()  # Копируем строку
            new_row["filename"] = new_img_path  # Обновляем путь к файлу
            augmented_rows.append(new_row)  # Добавляем новую строку в список

    # Объединяем исходные данные и аугментированные
    augmented_df = pd.concat([df, pd.DataFrame(augmented_rows)], ignore_index=True)

    augmented_df.to_csv(output_csv, index=False)  # Сохраняем в CSV
    print(f"Расширенный CSV файл сохранен в: {output_csv}")


# Задайте пути к входному и выходному файлам
input_csv_path = "description2.csv"  # Замените на путь к вашему csv-файлу
output_csv_path = "augmented_description2.csv"  # Путь к выходному CSV-файлу
output_images_dir = "/Working/data/"  # Директория для сохранения изображений
num_augmentations = 5  # Количество аугментаций для каждого изображения

# Вызов функции для расширения CSV-файла
augment_and_extend_csv(input_csv_path, output_csv_path, output_images_dir, num_augmentations)






Расширенный CSV файл сохранен в: augmented_description2.csv


Проверяем количество картинок в папке data после первой аугментации

In [12]:
import os

def count_images_in_directory(directory):
    """
    Подсчитывает количество файлов изображений в указанной директории.

    Args:
        directory (str): Путь к директории.

    Returns:
        int: Количество файлов изображений в директории.
    """
    image_extensions = ['.jpg', '.jpeg', '.png', '.gif', '.bmp']  # Add more if needed
    count = 0
    for filename in os.listdir(directory):
        if any(filename.lower().endswith(ext) for ext in image_extensions):
            count += 1
    return count


image_directory = "/Working/data/"

image_count = count_images_in_directory(image_directory)
print(f"Количество изображений в папке {image_directory}: {image_count}")

Количество изображений в папке /Working/data/: 10021


Расширяем датасет + 3 аугментации (размытие, яркость и контраст, шум) + описания.
на входе папка data c картинками после первой аугментации и файл augmented_description2.csv. На выходе увеличенное количество картинок в папке data и дополненный csv - augmented_description2_extended.csv

In [13]:
import pandas as pd
import os
import numpy as np
import cv2
from tensorflow.keras.preprocessing.image import load_img, img_to_array
import uuid
import random

def augment_image(img):
    """Применяет реалистичную аугментацию к изображению."""
    img = np.array(img, dtype=np.float32)
    rows, cols, ch = img.shape

    # Размытие (Разные уровни)
    if random.random() < 0.5:
        blur_size = random.choice([3, 5, 7])  # Случайный размер ядра
        img = cv2.GaussianBlur(img, (blur_size, blur_size), 0)

    # Яркость и контраст
    if random.random() < 0.5:
        brightness = random.uniform(0.7, 1.3)  # Более широкий диапазон
        contrast = random.uniform(0.7, 1.3)    # Более широкий диапазон
        img = cv2.convertScaleAbs(img, alpha=contrast, beta=0)
        img = cv2.add(img, np.array([brightness * 255 - 255 if brightness > 1 else 0], dtype=np.float32))

    # Шум
    if random.random() < 0.5:
        noise = np.random.normal(0, 25, img.shape)  # Гауссовский шум
        img = np.clip(img + noise, 0, 255)           # Обрезаем значения

    # Дополнительные аугментации (можно добавить при необходимости)
    # ...

    return np.uint8(img)


def augment_and_extend_csv(input_csv, output_csv, output_dir, augmentations_per_image=3):
    """Расширяет CSV-файл, добавляя аугментированные изображения."""
    df = pd.read_csv(input_csv)
    augmented_rows = []
    os.makedirs(output_dir, exist_ok=True)

    for index, row in df.iterrows():
        img_path = row["filename"]
        if not os.path.exists(img_path):
            print(f"Файл не найден: {img_path}")
            continue

        try:
            img = load_img(img_path, target_size=(224, 224))
            img = img_to_array(img)
        except Exception as e:
            print(f"Ошибка при загрузке изображения {img_path}: {e}")
            continue

        for i in range(augmentations_per_image):
            aug_img = augment_image(img)
            new_filename = f"{uuid.uuid4().hex}.jpg"
            new_img_path = os.path.join(output_dir, new_filename)
            cv2.imwrite(new_img_path, aug_img)

            new_row = row.copy()
            new_row["filename"] = new_img_path
            augmented_rows.append(new_row)

    # Append the new rows to the existing dataframe
    augmented_df = pd.concat([df, pd.DataFrame(augmented_rows)], ignore_index=True)
    augmented_df.to_csv(output_csv, index=False)
    print(f"Расширенный CSV файл сохранен в: {output_csv}")

# --- Настройка ---
input_csv_path = "augmented_description2.csv"  # Входной CSV (уже аугментированный)
output_csv_path = "augmented_description2_extended.csv"  # Выходной CSV
output_images_dir = "/Working/data/"  # Каталог для новых аугментированных изображений
augmentations_per_image = 3 # Количество дополнительных аугментаций

# --- Выполнение ---
augment_and_extend_csv(input_csv_path, output_csv_path, output_images_dir, augmentations_per_image)

Расширенный CSV файл сохранен в: augmented_description2_extended.csv


Проверяем количество картинок в папке data после второй аугментации

In [14]:
import os

def count_images_in_directory(directory):
    """
    Подсчитывает количество файлов изображений в указанной директории.

    Args:
        directory (str): Путь к директории.

    Returns:
        int: Количество файлов изображений в директории.
    """
    image_extensions = ['.jpg', '.jpeg', '.png', '.gif', '.bmp']  # Add more if needed
    count = 0
    for filename in os.listdir(directory):
        if any(filename.lower().endswith(ext) for ext in image_extensions):
            count += 1
    return count


image_directory = "/Working/data/"

image_count = count_images_in_directory(image_directory)
print(f"Количество изображений в папке {image_directory}: {image_count}")

Количество изображений в папке /Working/data/: 40081


датасет сформирован

Модель (readme.docx)

Сохраняем модель в файл (26 минут), извлекаем признаки из изображений, поиск ближайшего соседа по косинусному расстоянию, пример

In [3]:
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from tensorflow.keras.applications import VGG16
from tensorflow.keras.models import Model
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
import numpy as np
import os

# 1. Загрузка данных
df = pd.read_csv("augmented_description2_extended.csv")

# 2. Предобработка изображений
def preprocess_images(df):
   
    images_list = []
    for index, row in df.iterrows():
        img_path = row["filename"]
        try:
            img = load_img(img_path, target_size=(224, 224))  # Загрузка изображения и изменение размера
            img = img_to_array(img) / 255.0  # Преобразование в numpy массив и нормализация (значения от 0 до 1)
            images_list.append(img)
        except Exception as e:
            print(f"Ошибка при загрузке изображения {img_path}: {e}")  # Вывод сообщения об ошибке, если изображение не удалось загрузить
            continue
    return np.array(images_list)  # Возвращает numpy массив предобработанных изображений

images = preprocess_images(df) # Применение функции предобработки к данным

# 3. Создание модели VGG16 для извлечения признаков (без верхних слоев)
base_model = VGG16(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
# Замораживаем веса базовой модели VGG16
for layer in base_model.layers:
    layer.trainable = False # Отключаем возможность обучения слоев VGG16

# Создаем новую модель, используя выходные данные VGG16
x = layers.Flatten()(base_model.output) # Преобразует многомерный тензор в одномерный
x = layers.Dense(128, activation='relu')(x)  # Добавляем свой полносвязный слой (Dense layer) с 128 нейронами и функцией активации ReLU
feature_extraction_model = Model(inputs=base_model.input, outputs=x) # Создание модели, вход которой - вход VGG16, выход - выход добавленного слоя

# Сохранение модели в файл
model_filename = "feature_extraction_model.h5"
feature_extraction_model.save(model_filename)
print(f"Модель сохранена в файл: {model_filename}")

# 4. Извлечение признаков из изображений
image_features = feature_extraction_model.predict(images) # Получение признаков для всех изображений в датасете

# 5. Функция для поиска ближайшего соседа по косинусному расстоянию
def find_closest_image(query_image_path, image_features, df):
  
    try:
        query_img = load_img(query_image_path, target_size=(224, 224)) # Загрузка и изменение размера изображения
        query_img = img_to_array(query_img) / 255.0 # Преобразование в numpy массив и нормализация
        query_img = np.expand_dims(query_img, axis=0) # Добавление размерности батча (делаем из одного изображения "батч" из одного изображения)

        query_features = feature_extraction_model.predict(query_img) # Получение признаков для входного изображения
        similarity_scores = cosine_similarity(query_features, image_features) # Вычисление косинусного расстояния между признаками входного изображения и признаками всех изображений в датасете

        closest_image_index = np.argmax(similarity_scores) # Определение индекса изображения с максимальным косинусным сходством

        closest_image_description = df.iloc[closest_image_index]["GPT4DESC"] # Получение описания наиболее похожего изображения
        closest_image_title = df.iloc[closest_image_index]["ru_title"] # Получение названия наиболее похожего изображения
        closest_image_author = df.iloc[closest_image_index]["ru_author"] # Получение автора наиболее похожего изображения

        return closest_image_title, closest_image_author, closest_image_description # Возвращает название, автора и описание наиболее похожего изображения

    except Exception as e:
        print(f"Ошибка при поиске ближайшего изображения: {e}") # Вывод сообщения об ошибке, если что-то пошло не так
        return None, None, None

# 6. Пример использования
query_image_path = "222.jpg"  # Путь к изображению, для которого ищем похожее

closest_title, closest_author, closest_description = find_closest_image(query_image_path, image_features, df) # Поиск наиболее похожего изображения

if closest_title and closest_author and closest_description: # Проверка, что все значения были найдены
    print("Найденное изображение:")
    print(f"Название: {closest_title}") # Вывод названия найденного изображения
    print(f"Автор: {closest_author}") # Вывод автора найденного изображения
    print(f"Описание: {closest_description}") # Вывод описания найденного изображения
else:
    print("Не удалось найти похожее изображение.") # Вывод сообщения, если не удалось найти похожее изображение

Модель сохранена в файл: feature_extraction_model.h5
1253/1253 ━━━━━━━━━━━━━━━━━━━━ 1454s 1s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 159ms/step
Найденное изображение:
Название: Дочь художника. 1923
Автор: Петров-Водкин Кузьма Сергеевич
Описание: Картина "Дочь художника" была написана Кузьмой Сергеевичем Петровым-Водкиным в 1923 году, в период значительных перемен в художественном мире и советской России. Это произведение отражает уникальный стиль Петрова-Водкина, сочетающий элементы символизма и модернизма. 

На картине изображена дочь художника, Елена Петрова-Водкина, что придаёт работе личный и интимный характер. Художник использует характерные для него мягкие, но насыщенные колористические решения с преобладанием теплых тонов. Его внимание к деталям и экспрессивное использование света создают особую атмосферу, заставляющую зрителя погружаться в изображённый мир.

Особенности композиции включают полукруглые линии и плавные формы, что создаёт гармоничное и уравновешенное изображение. Петров-

In [4]:
# 6. Пример использования
query_image_path = "555.jpg"  # Путь к изображению, для которого ищем похожее

closest_title, closest_author, closest_description = find_closest_image(query_image_path, image_features, df) # Поиск наиболее похожего изображения

if closest_title and closest_author and closest_description: # Проверка, что все значения были найдены
    print("Найденное изображение:")
    print(f"Название: {closest_title}") # Вывод названия найденного изображения
    print(f"Автор: {closest_author}") # Вывод автора найденного изображения
    print(f"Описание: {closest_description}") # Вывод описания найденного изображения
else:
    print("Не удалось найти похожее изображение.") # Вывод сообщения, если не удалось найти похожее изображение

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 156ms/step
Найденное изображение:
Название: Севилья. Альказар. 1910
Автор: Василий Иванович Суриков
Описание: Картина "Севилья. Альказар. 1910" Василия Ивановича Сурикова представляет собой атмосферный этюд, созданный художником во время его поездки в Испанию. В этот период Суриков активно изучал произведения великих мастеров Европы, ищя вдохновение в местной архитектуре и культуре. Альказар в Севилье, будучи одним из самых старых дворцов в Европе, стал отличным источником для погружения в богатую историю и колорит Испании.

Картина выполнена в импрессионистской манере, что для Сурикова являлось экспериментом, поскольку он был известен прежде всего своими историческими картинами. Художник применяет светлую палитру и свободные мазки, чтобы передать игру света и тени на стенах и садах Альказара. Это произведение отличается от более крупных и детализированных полотен Сурикова своим камерным характером и акцентом на атмосферу и настроение.

Суриков стремится пер

Признаки извлекались и сохранялись в файл 552 минуты. 

In [9]:
import tensorflow as tf
from tensorflow.keras.preprocessing.image import load_img, img_to_array
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
import numpy as np
import os
import time
import pickle  # Для сохранения и загрузки признаков

# 1. Загрузка данных
df = pd.read_csv("augmented_description2_extended.csv")

# 2. Определение функции для предобработки новых изображений
def preprocess_new_image(image_path):
    """
    Загружает, изменяет размер и нормализует одно изображение.
    """
    try:
        img = load_img(image_path, target_size=(224, 224))
        img = img_to_array(img) / 255.0  # Нормализация
        img = np.expand_dims(img, axis=0)  # Добавление размерности батча
        return img
    except Exception as e:
        print(f"Ошибка при загрузке изображения {image_path}: {e}")
        return None

# 3. Загрузка предварительно обученной модели
model_filename = "feature_extraction_model.h5"
try:
    feature_extraction_model = tf.keras.models.load_model(model_filename)
    # Компиляция модели (важно после загрузки, если модель будет использоваться для обучения или оценки)
    feature_extraction_model.compile(optimizer='adam', loss='mse')
    print(f"Модель успешно загружена и скомпилирована из файла: {model_filename}")
except Exception as e:
    print(f"Ошибка при загрузке модели из файла {model_filename}: {e}")
    exit()

# 4. Извлечение и сохранение признаков всего датасета (выполняется только один раз!)
features_filename = "image_features.pkl" # Имя файла для сохранения признаков

if not os.path.exists(features_filename):
    print("Извлечение признаков для всего датасета...")
    image_features_list = []
    for index, row in df.iterrows():
        img_path = row["filename"]
        try:
            img = load_img(img_path, target_size=(224, 224))
            img = img_to_array(img) / 255.0
            img = np.expand_dims(img, axis=0)
            features = feature_extraction_model.predict(img)
            image_features_list.append(features)
        except Exception as e:
            print(f"Ошибка при извлечении признаков для {img_path}: {e}")
            image_features_list.append(None) # или другой способ обработки ошибки
    image_features = np.concatenate(image_features_list, axis=0) # Объединение в один numpy массив
    with open(features_filename, "wb") as f:
        pickle.dump(image_features, f)  # Сохранение признаков в файл
    print(f"Признаки всего датасета сохранены в файл: {features_filename}")
else:
    print(f"Загрузка признаков всего датасета из файла: {features_filename}")
    with open(features_filename, "rb") as f:
        image_features = pickle.load(f)  # Загрузка признаков из файла

# 5. Функция для поиска ближайшего соседа (использует предварительно извлеченные признаки)
def find_closest_image(image_path, image_features, df, model):
    """
    Находит наиболее похожее изображение в датасете на основе косинусного расстояния между признаками.

    Аргументы:
        image_path: Путь к изображению, для которого нужно найти похожее.
        image_features: Матрица признаков для всех изображений в датасете (предварительно извлеченная).
        df: DataFrame с информацией об изображениях (название, автор, описание).
        model: Загруженная модель для извлечения признаков (не используется, но оставлена для совместимости).

    Возвращает:
        Кортеж: (название, автор, описание) наиболее похожего изображения, или (None, None, None) в случае ошибки.
    """
    try:
        # Предобработка нового изображения
        new_img = preprocess_new_image(image_path)

        if new_img is None:
            return None, None, None

        # Извлечение признаков для нового изображения
        new_features = model.predict(new_img)

        # Вычисление косинусного сходства
        similarity_scores = cosine_similarity(new_features, image_features) # Вычисляем косинусное сходство

        # Поиск наиболее похожего изображения
        closest_image_index = np.argmax(similarity_scores)

        # Получение информации о наиболее похожем изображении
        closest_image_description = df.iloc[closest_image_index]["GPT4DESC"]
        closest_image_title = df.iloc[closest_image_index]["ru_title"]
        closest_image_author = df.iloc[closest_image_index]["ru_author"]

        return closest_image_title, closest_image_author, closest_image_description
    except Exception as e:
        print(f"Ошибка при поиске ближайшего изображения: {e}")
        return None, None, None

# 6. Пример использования
new_image_path = "222.jpg"  # Замените на путь к вашему тестовому изображению

# Поиск наиболее похожего изображения (использует предварительно извлеченные признаки)
start_time = time.time()
closest_title, closest_author, closest_description = find_closest_image(new_image_path, image_features, df, feature_extraction_model)
end_time = time.time()
print(f"Общее время поиска похожего изображения: {end_time - start_time:.2f} секунд")

if closest_title and closest_author and closest_description:
    print("Найденное изображение:")
    print(f"Название: {closest_title}")
    print(f"Автор: {closest_author}")
    print(f"Описание: {closest_description}")
else:
    print("Не удалось найти похожее изображение.")

Модель успешно загружена и скомпилирована из файла: feature_extraction_model.h5
Извлечение признаков для всего датасета...
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 744ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 139ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 141ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 142ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 135ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 148ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 145ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 147ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 143ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 139ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 144ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 140ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 135ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 136ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 137ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 138ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 139ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 135ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 135ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 142ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 143ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 138ms/step
1/1 ━━━━━━━━━━━━━━━

In [10]:
# 6. Пример использования
new_image_path = "555.jpg"  # Замените на путь к вашему тестовому изображению

# Поиск наиболее похожего изображения (использует предварительно извлеченные признаки)
start_time = time.time()
closest_title, closest_author, closest_description = find_closest_image(new_image_path, image_features, df, feature_extraction_model)
end_time = time.time()
print(f"Общее время поиска похожего изображения: {end_time - start_time:.2f} секунд")

if closest_title and closest_author and closest_description:
    print("Найденное изображение:")
    print(f"Название: {closest_title}")
    print(f"Автор: {closest_author}")
    print(f"Описание: {closest_description}")
else:
    print("Не удалось найти похожее изображение.")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 184ms/step
Общее время поиска похожего изображения: 0.31 секунд
Найденное изображение:
Название: Севилья. Альказар. 1910
Автор: Василий Иванович Суриков
Описание: Картина "Севилья. Альказар. 1910" Василия Ивановича Сурикова представляет собой атмосферный этюд, созданный художником во время его поездки в Испанию. В этот период Суриков активно изучал произведения великих мастеров Европы, ищя вдохновение в местной архитектуре и культуре. Альказар в Севилье, будучи одним из самых старых дворцов в Европе, стал отличным источником для погружения в богатую историю и колорит Испании.

Картина выполнена в импрессионистской манере, что для Сурикова являлось экспериментом, поскольку он был известен прежде всего своими историческими картинами. Художник применяет светлую палитру и свободные мазки, чтобы передать игру света и тени на стенах и садах Альказара. Это произведение отличается от более крупных и детализированных полотен Сурикова своим камерным характером и акцен